This python code has been developped by [Taïs Grippa](https://github.com/tgrippa) (Université Libre de Bruxelles). 

Code developped on Ubuntu 22.04 (Ubuntu Jammy) and GRASS GIS 8.0.2 using the Docker environment [available here](https://github.com/tgrippa/Weaksupervision_Vaihingen).

# Define working environment

**Import libraries**

In [1]:
# Import libraries needed for setting parameters of operating system 
import os
import sys
import csv
import tempfile
import glob
import math
import pickle
import time 
print(sys.version)

3.10.4 (main, Jun 29 2022, 12:14:53) [GCC 11.2.0]


In [2]:
## Import multiprocessing and functools libraries
import multiprocessing
from multiprocessing import Pool
from functools import partial

**Add folder with SCR provided belong to this notebook**

In [3]:
# Add local module to the path
src = os.path.abspath(os.path.join(os.environ['HOME'],'github','SRC'))
if src not in sys.path:
    sys.path.append(src)

**Setup environment variables for TAIS DESKTOP (Linux Mint + GRASS Dev)**

Please edit the file in `../SRC/config.py`, containing the configuration parameters, according to your own computer setup. The following cell is used to run this file.



In [4]:
exec(open(os.path.join(os.environ['HOME'],'github','SRC', 'config.py')).read())

In [5]:
print(config_parameters)

{'GISBASE': '/usr/lib/grass78', 'PYTHONLIB': '/usr/bin/python3', 'gisdb': '/home/tais/GRASSDATA', 'location': 'flair-one', 'permanent_mapset': 'PERMANENT', 'locationepsg': '2154', 'outputfolder': '/home/tais/result', 'inputdir': '/home/tais/data'}


In [6]:
print(data)

{'legend': '/home/tais/github/Legend.txt'}


In [7]:
# Import functions that setup the environmental variables
import environ_variables as envi

In [8]:
# Set environmental variables
envi.setup_environmental_variables() 
# Display current environment variables of your computer
envi.print_environmental_variables()

PATH	= /.local/bin:/usr/local/sbin:/usr/local/bin:/usr/sbin:/usr/bin:/sbin:/bin:/usr/lib/grass78/bin:/usr/lib/grass78/script:/usr/lib/grass78/lib 	
HOSTNAME	= 2bec62b8c0f8 	
DISPLAY	= unix 	
LANG	= C.UTF-8 	
LC_ALL	= C.UTF-8 	
JUPYTER_ENABLE_LAB	= yes 	
TINI_VERSION	= v0.6.0 	
HOME	= /home/tais 	
GIT_PYTHON_REFRESH	= quiet 	
JPY_PARENT_PID	= 7 	
TERM	= xterm-color 	
CLICOLOR	= 1 	
PAGER	= cat 	
GIT_PAGER	= cat 	
MPLBACKEND	= module://matplotlib_inline.backend_inline 	
PYTHONPATH	= :/usr/lib/grass78/etc/python:/usr/lib/grass78/etc/python/grass:/usr/lib/grass78/etc/python/grass/script 	
LD_LIBRARY_PATH	= :/usr/lib/grass78/lib 	
GISBASE	= /usr/lib/grass78 	
PYTHONLIB	= /usr/bin/python3 	
GIS_LOCK	= $$ 	
GISRC	= /home/tais/.grass7/rc 	


**GRASS GIS Python libraries**

In [9]:
# Import libraries needed to launch GRASS GIS in the jupyter notebook
import grass.script.setup as gsetup
# Import libraries needed to call GRASS using Python
import grass.script as gscript

**Other functions**

In [10]:
from grass.script import vector
# Import function that check existance and create GRASS GIS database folder if needed
from grass_database import check_gisdb, check_location, check_mapset, working_mapset
# Import functions for processing time information
from processing_time import start_processing, print_processing_time
# Import function that generate a random name in the GRASS GIS environement
from random_layer_name import random_layer_name
# Import function that check and create folder
from mkdir import check_create_dir
# Import function that check if GRASS GIS add-on is installed and install it if needed
from gextension import check_install_addon
# Import function for sorting string number naturally
from sorting_natural import natural_keys

**-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-**

In [11]:
def launch_mapset(mapset):
    #Declare empty list that will contain the messages to return
    return_message = []
    # Init
    gsetup.init(config_parameters['GISBASE'], config_parameters['gisdb'], config_parameters['location'], mapset)
    # Check if the location exists and create it if not, with the CRS defined by the epsg code 
    return_message.append(check_location(config_parameters["gisdb"],config_parameters['location'],config_parameters["locationepsg"]))
    # Check if mapset exists
    return_message.append(check_mapset(config_parameters["gisdb"],config_parameters['location'],mapset))
    # Change the current working GRASS GIS session mapset
    return_message.append(working_mapset(config_parameters["gisdb"],config_parameters['location'],mapset))
    # Return
    return return_message

In [12]:
def segmentation(mapset):
    # Image ID
    image_id = int(mapset.split('_')[-1])
    # Define computational region
    gscript.run_command('g.region', overwrite=True, raster='red', save="region")
    # Define group of layers
    gscript.run_command('g.remove', quiet=True, flags='f', type='group', name='top')
    gscript.run_command('i.group', quiet=True, group='top', input="nir,red,green,blue")
    # gscript.run_command('i.group', group='top', input="nir,red,green,blue,ndsm") # TODO: Test of nDSM in the segmentation  
    # Unsupervised Segmentation parameter optimization 
    gscript.run_command('i.segment.uspo', quiet=True, overwrite=True, group='top', segment_map='best_segment', regions='region', segmentation_method='region_growing', 
                        threshold_start='0.005', threshold_stop='0.05', threshold_step='0.002', minsizes='50', memory='3000', processes='25')
    # Trick the segment ID to be sure the ID is unique through all the images
    formula = "segmentation = (%s*1000000) + best_segment_region_rank1"%image_id
    #formula = "segmentation = best_segment_region_rank1"
    gscript.mapcalc(formula, quiet=True, overwrite=True)
    # Exportation
    gscript.run_command('r.out.gdal', quiet=True, overwrite=True, flags='m', input='segmentation', 
                        output=os.path.join(config_parameters['outputfolder'],'segment_rast','segment_%s.tiff'%mapset), format='GTiff')

In [13]:
def compute_stats(mapset):
    # Define list of raster on which to compute statistics
    rast_layers=[]
    rast_layers.append('red')
    rast_layers.append('green')
    rast_layers.append('blue')
    rast_layers.append('nir')
    rast_layers.append('ndvi')
    rast_layers.append('ndsm')
    rast_layers.append('text_green_DE')
    rast_layers.append('text_green_Entr')
    rast_layers.append('text_red_ASM')
    rast_layers.append('text_red_IDM')
    rast_layers.append('text_nir_DE')
    # Define path to csv files 
    csv_output = os.path.join(config_parameters['outputfolder'],'stats', 'stats_%s.csv'%mapset)
    tmp_csv_output = os.path.join(config_parameters['outputfolder'],'stats', 'tmp_statszonal_%s.csv'%mapset)
    gpkg_output = os.path.join(config_parameters['outputfolder'],'segment_vect', 'segment_%s.gpkg'%mapset)
    
    # Define path to final csv with statistics
    compute_stats = os.path.join(config_parameters['outputfolder'],'compute_stats.sh')
    # Create csv
    with open(compute_stats, 'w') as csvf:
        # Write the bash script content to the file
        csvf.write('#!/bin/bash\n')
        csvf.write('# Read the script parameter that define the mapset to process\n')
        csvf.write('mapset="$1"\n')
        csvf.write('# Define the computational region\n')
        csvf.write('g.region raster=segmentation --overwrite\n')
        csvf.write('# Define the path to the final CSV with statistics\n')
        csvf.write('csv_output="/home/tais/result/stats/stats_${mapset}.csv"\n')
        csvf.write('# Compute segment statistics\n')
        content = "i.segment.stats --quiet --overwrite map=segmentation rast_layers='%s' "%','.join(rast_layers) 
        content += "raster_statistics='stddev,coeff_var,sum,median,perc_90' area_measures='area,perimeter,compact_circle,compact_square,fd'"
        content += "csvfile=%s vectormap=segment processes=20\n"%csv_output
        csvf.write(content)
        csvf.write('# Compute mode of GTS (Ground truth label)\n')
        content = "r.zonal.classes --overwrite zone_map=segmentation raster=gts statistics=mode csvfile=%s separator=comma"%tmp_csv_output
        csvf.write(content)
        csvf.write('# Import csv as table and join to attribute table with segment statistics\n')
        csvf.write('db.in.ogr --overwrite input=%s output=tmp_table\n'%tmp_csv_output)
        csvf.write('v.db.join --quiet map=segment column=cat other_table="tmp_table" other_column=cat_ subset_columns=mode\n')
        csvf.write('v.db.renamecolumn --quiet map=segment column="mode,gts_label"\n')
        csvf.write('rm %s\n'%tmp_csv_output)
        csvf.write('v.out.ogr --quiet --overwrite input=segment output=%s format=GPKG"\n'%gpkg_output)
        csvf.write('v.db.select --quiet --overwrite map=segment separator=comma file=%s\n'%csv_output)

---------------------------------------

## Create new directories

In [14]:
# Check and create folder if needed
check_create_dir(config_parameters['outputfolder'])
check_create_dir(os.path.join(config_parameters['outputfolder'],'stats'))
check_create_dir(os.path.join(config_parameters['outputfolder'],'segment_rast'))
check_create_dir(os.path.join(config_parameters['outputfolder'],'segment_vect'))

The folder '/home/tais/result' already exists
The folder '/home/tais/result/stats' already exists
The folder '/home/tais/result/segment_rast' already exists
The folder '/home/tais/result/segment_vect' already exists


---------------------------------------

## Create bash script to compute statistics

In [43]:
# Define list of raster on which to compute statistics
rast_layers=[]
rast_layers.append('red')
rast_layers.append('green')
rast_layers.append('blue')
rast_layers.append('nir')
rast_layers.append('ndvi')
rast_layers.append('ndsm')
rast_layers.append('text_green_DE')
rast_layers.append('text_green_Entr')
rast_layers.append('text_red_ASM')
rast_layers.append('text_red_IDM')
rast_layers.append('text_nir_DE')
# Define path to csv files 
csv_output = os.path.join(config_parameters['outputfolder'],'stats', 'stats_${mapset}.csv')
tmp_csv_output = os.path.join(config_parameters['outputfolder'],'stats', 'tmp_statszonal_${mapset}.csv')
gpkg_output = os.path.join(config_parameters['outputfolder'],'segment_vect', 'segment_${mapset}.gpkg')

# Define path to final csv with statistics
compute_stats = os.path.join(config_parameters['outputfolder'],'compute_stats.sh')
# Create csv
with open(compute_stats, 'w') as csvf:
    # Write the bash script content to the file
    csvf.write('#!/bin/bash\n')
    csvf.write('# Read the script parameter that define the mapset to process\n')
    csvf.write('mapset="$1"\n\n')
    csvf.write('# Define the computational region\n')
    csvf.write('g.region raster=segmentation --overwrite\n\n')
    csvf.write('# Define the path to the final CSV with statistics\n')
    csvf.write('csv_output="/home/tais/result/stats/stats_${mapset}.csv"\n\n')
    csvf.write('# Compute segment statistics\n')
    content = "i.segment.stats --quiet --overwrite map=segmentation rasters='%s' "%','.join(rast_layers) 
    content += "raster_statistics='stddev,coeff_var,sum,median,perc_90' area_measures='area,perimeter,compact_circle,compact_square,fd' "
    content += "csvfile=%s vectormap=segment processes=20\n\n"%csv_output
    csvf.write(content)
    csvf.write('# Compute mode of GTS (Ground truth label)\n')
    content = "r.zonal.classes --quiet --overwrite zone_map=segmentation raster=gts statistics=mode csvfile=%s separator=comma\n\n"%tmp_csv_output
    csvf.write(content)
    csvf.write('# Import csv as table and join to attribute table with segment statistics\n')
    csvf.write('db.in.ogr --quiet --overwrite input=%s output=tmp_table\n\n'%tmp_csv_output)
    csvf.write('v.db.join --quiet map=segment column=cat other_table="tmp_table" other_column=cat_ subset_columns=mode\n\n')
    csvf.write('v.db.renamecolumn --quiet map=segment column="mode,gts_label"\n\n')
    csvf.write('rm %s\n\n'%tmp_csv_output)
    csvf.write('v.out.ogr --quiet --overwrite input=segment output=%s format=GPKG\n\n'%gpkg_output)
    csvf.write('v.db.select --quiet --overwrite map=segment separator=comma file=%s\n\n'%csv_output)

---------------------------------------

# Get list of mapset to process

In [15]:
import fnmatch

def find_files(path, pattern):
    for root, dirs, files in os.walk(path):
        for file in fnmatch.filter(files, pattern):
            yield os.path.join(root, file)

In [16]:
# Get a list of path to train images
train_folder = os.path.join(config_parameters['inputdir'],'train')
list_mapsets = [os.path.split(x)[-1].split('.tif')[0] for x in find_files(train_folder, "IMG_*.tif")]

In [17]:
print(f'There are {len(list_mapsets)} train images')

There are 2950 train images


---------------------------------------

In [59]:
list_mapsets[:2]

['IMG_027772', 'IMG_027782']

# Segmentation (region growing)

In [61]:
import subprocess

def worker_segmentation(mapset):
    # Launch a new mapset for this image
    launch_mapset(mapset)
    # Segmentation
    segmentation(mapset)

In [37]:
worker("IMG_028759")

In [ ]:
for mapset in list_mapsets[:5]:
    # Launch a new mapset for this image
    launch_mapset(mapset)
    # Segmentation
    segmentation(mapset)

# Compute stats

**TODO: Still need to fix. Impossible to run the compute_stats.sh from the jupyter notebook (works from terminal)**

In [73]:
def worker_compute_stats(mapset): 
    process = subprocess.Popen(['grass', '/home/tais/GRASSDATA/flair-one/%s'%mapset,
                             '--exec', 'bash /home/tais/result/compute_stats.sh %s'%mapset])
    process.wait()

In [82]:
subprocess.Popen(['grass', '/home/tais/GRASSDATA/flair-one/%s'%list_mapsets[0],
                             '--exec', 'bash', '/home/tais/result/compute_stats.sh %s'%list_mapsets[0]])

<Popen: returncode: None args: ['grass', '/home/tais/GRASSDATA/flair-one/IMG...>

Starting GRASS GIS...
Cleaning up temporary files...
Executing <bash /home/tais/result/compute_stats.sh IMG_027772> ...
bash: /home/tais/result/compute_stats.sh IMG_027772: No such file or directory
Execution of <bash /home/tais/result/compute_stats.sh IMG_027772> finished.
Cleaning up default sqlite database ...
Cleaning up temporary files...


In [74]:
for mapset in list_mapsets[:5]:
    worker_compute_stats(mapset)

Starting GRASS GIS...
Cleaning up temporary files...
Executing <bash /home/tais/result/compute_stats.sh IMG_027772> ...
ERROR: Execution of <bash /home/tais/result/compute_stats.sh IMG_027772> failed:
[Errno 2] No such file or directory: 'bash /home/tais/result/compute_stats.sh IMG_027772'
Exiting...
Starting GRASS GIS...
Cleaning up temporary files...
Executing <bash /home/tais/result/compute_stats.sh IMG_027782> ...
ERROR: Execution of <bash /home/tais/result/compute_stats.sh IMG_027782> failed:
[Errno 2] No such file or directory: 'bash /home/tais/result/compute_stats.sh IMG_027782'
Exiting...
Starting GRASS GIS...
Cleaning up temporary files...
Executing <bash /home/tais/result/compute_stats.sh IMG_027769> ...
ERROR: Execution of <bash /home/tais/result/compute_stats.sh IMG_027769> failed:
[Errno 2] No such file or directory: 'bash /home/tais/result/compute_stats.sh IMG_027769'
Exiting...
Starting GRASS GIS...
Cleaning up temporary files...
Executing <bash /home/tais/result/compute

In [ ]:
# Launch processes in parallel
start_parallel = start_processing()
ncores = 10
p = Pool(ncores)
output = p.map(worker, list_mapsets[:])  # Launch the processes for as many items in the list (if function with a return, the returned results are ordered thanks to 'map' function)
p.close()
p.join()
# Print
print_processing_time(start_parallel, "Computation (on %s cores) achieved in "%(ncores))

Cleaning up temporary files...
Done.

Goodbye from GRASS GIS


          __________  ___   __________    _______________
         / ____/ __ \/   | / ___/ ___/   / ____/  _/ ___/
        / / __/ /_/ / /| | \__ \\_  \   / / __ / / \__ \
       / /_/ / _, _/ ___ |___/ /__/ /  / /_/ // / ___/ /
       \____/_/ |_/_/  |_/____/____/   \____/___//____/

Welcome to GRASS GIS 7.8.7
GRASS GIS homepage:                      https://grass.osgeo.org
This version running through:            Bourne Shell (sh)
Help is available with the command:      g.manual -i
See the licence terms with:              g.version -c
See citation options with:               g.version -x
Start the GUI with:                      g.gui wxpython
When ready to quit enter:                exit

Cleaning up temporary files...
Starting GRASS GIS...
Cleaning up temporary files...
Done.

Goodbye from GRASS GIS

Cleaning up temporary files...

          __________  ___   __________    _______________
         / ____/ __ \/   | / _

In [26]:
mapset = list_mapsets[0] 

subprocess.run(['grass', '/home/tais/GRASSDATA/flair-one/%s'%mapset,
                             '--exec', 'bash /home/tais/compute_stats.sh %s'%mapset], shell=True, capture_output=False, text=False)

Starting GRASS GIS...
Cleaning up temporary files...

          __________  ___   __________    _______________
         / ____/ __ \/   | / ___/ ___/   / ____/  _/ ___/
        / / __/ /_/ / /| | \__ \\_  \   / / __ / / \__ \
       / /_/ / _, _/ ___ |___/ /__/ /  / /_/ // / ___/ /
       \____/_/ |_/_/  |_/____/____/   \____/___//____/

Welcome to GRASS GIS 7.8.7
GRASS GIS homepage:                      https://grass.osgeo.org
This version running through:            Bourne Shell (sh)
Help is available with the command:      g.manual -i
See the licence terms with:              g.version -c
See citation options with:               g.version -x
Start the GUI with:                      g.gui wxpython
When ready to quit enter:                exit

Cleaning up default sqlite database ...
Cleaning up temporary files...
Done.

Goodbye from GRASS GIS



CompletedProcess(args=['grass', '/home/tais/GRASSDATA/flair-one/IMG_027772', '--exec', 'bash /home/tais/compute_stats.sh IMG_027772'], returncode=0)

# Merge geopackages of images from the same zone

In [65]:
import pandas as pd
import geopandas as gpd

In [73]:
# Path to the GeoPackage file
gpkg_file = '/home/tais/data/Train_test_split.gpkg'
# Read the GeoPackage file
df = gpd.read_file(gpkg_file)
# Filter only rows where 'Train_test' = "Train"
df = df[df['Train_test']=="train"]

In [74]:
# Display attibute table
df.head(15)

_key     domain   zone  patch_centroid_x  patch_centroid_y  \
27537  IMG_027538  D044_2020  Z1_AA          372483.2         6689044.8   
27538  IMG_027539  D044_2020  Z1_AA          372585.6         6689044.8   
27539  IMG_027540  D044_2020  Z1_AA          372688.0         6689044.8   
27540  IMG_027541  D044_2020  Z1_AA          372790.4         6689044.8   
27541  IMG_027542  D044_2020  Z1_AA          372892.8         6689044.8   
27542  IMG_027543  D044_2020  Z1_AA          372995.2         6689044.8   
27543  IMG_027544  D044_2020  Z1_AA          373097.6         6689044.8   
27544  IMG_027545  D044_2020  Z1_AA          373200.0         6689044.8   
27545  IMG_027546  D044_2020  Z1_AA          373302.4         6689044.8   
27546  IMG_027547  D044_2020  Z1_AA          373404.8         6689044.8   
27547  IMG_027548  D044_2020  Z1_AA          372483.2         6688942.4   
27548  IMG_027549  D044_2020  Z1_AA          372585.6         6688942.4   
27549  IMG_027550  D044_2020  Z1_AA          372688.0         6688942.4   
27550  IMG_027551  D044_2020  Z1_AA          372790.4         6688942.4   
27551  IMG_027552  D044_2020  Z1_AA          372892.8         6688942.4   

       patch_centroid_z        date   time       camera Train_test  \
27537         25.580000  2020-05-27  09h56  UCE-M3-f120      train   
27538         26.799999  2020-05-27  09h56  UCE-M3-f120      train   
27539         28.520000  2020-05-27  09h56  UCE-M3-f120      train   
27540         30.790001  2020-05-27  09h56  UCE-M3-f120      train   
27541         33.330002  2020-05-27  09h56  UCE-M3-f120      train   
27542         37.110001  2020-05-27  09h56  UCE-M3-f120      train   
27543         40.000000  2020-05-27  09h56  UCE-M3-f120      train   
27544         40.820000  2020-05-27  09h56  UCE-M3-f120      train   
27545         42.500000  2020-05-27  09h56  UCE-M3-f120      train   
27546         44.000000  2020-05-27  09h56  UCE-M3-f120      train   
27547         30.580000  2020-05-27  09h56  UCE-M3-f120      train   
27548         33.900002  2020-05-27  09h56  UCE-M3-f120      train   
27549         36.259998  2020-05-27  09h56  UCE-M3-f120      train   
27550         39.720001  2020-05-27  09h56  UCE-M3-f120      train   
27551         42.439999  2020-05-27  09h56  UCE-M3-f120      train   

                             geometry  
27537  POINT (372483.200 6689044.800)  
27538  POINT (372585.600 6689044.800)  
27539  POINT (372688.000 6689044.800)  
27540  POINT (372790.400 6689044.800)  
27541  POINT (372892.800 6689044.800)  
27542  POINT (372995.200 6689044.800)  
27543  POINT (373097.600 6689044.800)  
27544  POINT (373200.000 6689044.800)  
27545  POINT (373302.400 6689044.800)  
27546  POINT (373404.800 6689044.800)  
27547  POINT (372483.200 6688942.400)  
27548  POINT (372585.600 6688942.400)  
27549  POINT (372688.000 6688942.400)  
27550  POINT (372790.400 6688942.400)  
27551  POINT (372892.800 6688942.400)

In [77]:
# Get list of images for each zones using "group by" and store it in a dictionnary 
df2 = df.groupby('zone')['_key'].apply(list)
dict_zone_images = df2.to_dict()

In [79]:
list_img_gfd = []
#for DOM in dict_domain_images.keys():
for ZONE in dict_zone_images.keys():
    print('Processing zone %s'%ZONE)
    for IMG in dict_zone_images[ZONE][:]:
        gpkg_file = '/home/tais/result/segment_vect/segment_%s.gpkg'%IMG
        # Read the GeoPackage file
        gdf_img = gpd.read_file(gpkg_file)
        # Append to the list
        list_img_gfd.append(gdf_img)
    # Contactenate all dataframes from the same domain
    gdf_domain = gpd.GeoDataFrame(pd.concat(list_img_gfd, ignore_index=True))
    # Save as GPKG
    out_file = '/home/tais/result/segment_vect/segment_%s.gpkg'%ZONE
    gdf_domain.to_file(out_file, layer=ZONE, driver="GPKG")

Processing zone Z10_NN


/home/tais/.local/lib/python3.10/site-packages/geopandas/io/file.py:572: UserWarning: You are attempting to write an empty DataFrame to file. For some drivers, this operation may fail.
  _to_file_fiona(df, filename, driver, schema, crs, mode, **kwargs)


Processing zone Z11_UU
Processing zone Z12_AN
Processing zone Z13_UU
Processing zone Z14_UU
Processing zone Z15_UF
Processing zone Z15_UU
Processing zone Z16_UA
Processing zone Z16_UF
Processing zone Z17_UA
Processing zone Z17_UU
Processing zone Z18_UN
Processing zone Z18_UU
Processing zone Z19_UU
Processing zone Z1_AA
Processing zone Z20_AU
Processing zone Z20_UU
Processing zone Z21_UN
Processing zone Z21_UU
Processing zone Z22_UU
Processing zone Z23_UA
Processing zone Z23_UU
Processing zone Z24_UU
Processing zone Z25_UU
Processing zone Z26_AA
Processing zone Z27_UU
Processing zone Z28_UU
Processing zone Z29_UN
Processing zone Z2_AU
Processing zone Z2_UN
Processing zone Z30_UU
Processing zone Z31_NN
Processing zone Z32_UU
Processing zone Z3_UN
Processing zone Z4_UU
Processing zone Z5_UF
Processing zone Z5_UU
Processing zone Z6_UU
Processing zone Z7_FF
Processing zone Z7_UU
Processing zone Z8_UF
Processing zone Z8_UU
Processing zone Z9_UF
Processing zone Z9_UU
